## Import

In [1]:
import drawsvg as dw
from pathlib import Path
from fetcher import Fetcher
from drawer import createGDFGroup, createGDFGroupWays

## Constants

In [2]:
#minx, miny, maxx,maxy
bbox = [2.163500, 41.358617, 2.209214, 41.424001,]
place_name = "barcelona"
theme_name = "Minimalistic_Japanese_Style"
SAVE_PATH = Path("renders") / place_name / f"{theme_name}.svg"
#24x36''
WIDTH = 3000 
HEIGHT = 4500

TEMPLATE_BG_FILL = '#241c1c'

TEMPLATE_FRAME = {
    'fill': '#eef5c0',
    'offset': 100,
    'width': 10,
}

BOTTOM_AREA_HEIGHT = 300

MAIN_TEXT = {
    'text': "KRAKÓW",
    'font_size': 108,
    'font_family': 'Dancing Script',
    'fill': '#ffffff',
}

SUB_TEXT = {
    'text': "Poland",
    'font_size': 72,
    'font_family': 'Dancing Script',
    'y_offset': 100,
    'fill': '#ffffff',
}

WATER_FILL = '#D4F1F9'
GREEN_FILL = '#DCECCB'
LAND_FILL = '#F3E3AC'

In [3]:
f = Fetcher(bbox_cords=bbox)

In [4]:


map_space = dw.Mask()
map_space.append(
    dw.Rectangle(0, 0, WIDTH, HEIGHT, fill='white'))

map_space_offset = TEMPLATE_FRAME['offset'] + TEMPLATE_FRAME['width']
map_space_width = WIDTH-(2*map_space_offset)
map_space_height = HEIGHT-(2*map_space_offset)-BOTTOM_AREA_HEIGHT

map_space_dims = [map_space_offset, map_space_offset, map_space_width, map_space_height]

map_space.append(
    dw.Rectangle(*map_space_dims, fill='black'))


template = dw.Group(id='template', mask=map_space)

In [5]:
bg = dw.Rectangle(0, 0, WIDTH, HEIGHT, id='bg', fill=TEMPLATE_BG_FILL)
template.append(bg)

tf = dw.Rectangle(TEMPLATE_FRAME['offset'], TEMPLATE_FRAME['offset'], WIDTH-(2*TEMPLATE_FRAME['offset']), HEIGHT-(2*TEMPLATE_FRAME['offset'])-BOTTOM_AREA_HEIGHT, id='frame', fill=TEMPLATE_FRAME['fill'])
template.append(tf)

In [6]:
text_area = dw.Group(id='text_area')

text_x = map_space_offset
text_y = map_space_height + 2.5*map_space_offset

text_area.append(dw.Text(MAIN_TEXT['text'], font_size=MAIN_TEXT['font_size'], x=text_x, y=text_y, id='main_text', fill=MAIN_TEXT['fill']))

text_y += SUB_TEXT['y_offset']
text_area.append(dw.Text(SUB_TEXT['text'], font_size=SUB_TEXT['font_size'], x=text_x, y=text_y, id='sub_text', fill=SUB_TEXT['fill']))

template.append(text_area)

## VARIABLES TO PUT MAP ON POSTER

In [7]:
map_width, map_height = f.size

# hole-width
s1 = map_space_width/map_width

# hole-heigh
s2 = map_space_height/map_height

s = max(s1,s2)

In [8]:
map_space_center_x = map_space_offset + map_space_width/2
map_space_center_y = map_space_offset + map_space_height/2

In [9]:
def scaleToPoster(gdf):
    gdf['geometry'] = (gdf['geometry']
        .translate(xoff=-f.centroid_mercator.x, yoff=-f.centroid_mercator.y)

        # inverse Y- axis
        .scale(xfact=1, yfact=-1, zfact=1.0, origin=(0, 0))

        # scale to fit poster
        .scale(xfact=s, yfact=s, zfact=1.0, origin=(0, 0))

        # shift to poster center
        .translate(xoff=map_space_center_x, yoff=map_space_center_y))
    
    return gdf

## RETRIEVING DATA

## APPEND TO MAP

In [10]:

#clip mam content
clip = dw.ClipPath()
clip.append(dw.Rectangle(*map_space_dims))
map_content = dw.Group(id='map', stroke='none', clip_path = clip)

## LAYERS

In [11]:
# land layer
map_content.append(dw.Rectangle(0, 0, WIDTH, HEIGHT, id='land', fill=LAND_FILL))

# water layer
water = scaleToPoster(f.waterGDF)
map_content.append(createGDFGroup(water, fill=WATER_FILL, id='water'))

#green
tags = {
    "leisure": 'park',
    "landuse": 'forest'
}
green = scaleToPoster(f.get_osmGDF(tags))
map_content.append(createGDFGroup(green, fill=GREEN_FILL, id='green'))



Retrieving sea water polygons
Sea water polygons retrieved
Sea water transformed
Inland water retrieved
Appended
Water merged


/home/olek/IT/dev/goa/goa_mapper/fetcher.py:100: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = sea_water_gdf.append(inland_water_gdf)


In [12]:
#streets
streets_gdf = scaleToPoster(f.streetsGDF)
map_content.append(createGDFGroupWays(streets_gdf, id='streets'))


In [13]:
d = dw.Drawing(WIDTH, HEIGHT, id_prefix='poster')

d.append(map_content)
d.append(template)
d.save_svg(SAVE_PATH)

In [14]:
d